In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline

import os.path
from pandas_ods_reader import read_ods

from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LogisticRegression

from keras.models import Sequential
from keras.layers import Dense
from keras import regularizers

import pydot
from IPython.display import SVG
from keras.utils.vis_utils import model_to_dot
from keras.utils import plot_model

%matplotlib inline

Using TensorFlow backend.


In [2]:
fighter_sheet = "raw_fighter_details"
fight_sheet = "raw_total_fight_data"

fighters_ods = "UFC-DATA-DELETE-LATER/raw_fighter_details.ods"
fights_ods = "UFC-DATA-DELETE-LATER/raw_total_fight_data.ods"

In [3]:
fights_data = read_ods(fights_ods, fight_sheet)
fighters_data = read_ods(fighters_ods, fighter_sheet)

In [4]:
fighters_data.head()

fighter_name  Height    Weight Reach Stance   DOB
0   AJ Fonseca   5' 4"  145 lbs.  None   None  None
1  AJ Matthews  5' 11"  185 lbs.  None   None  None
2     AJ McKee  5' 10"  145 lbs.  None   None  None
3    AJ Siscoe   5' 7"  135 lbs.  None   None  None
4   Aalon Cruz   6' 0"  145 lbs.  None   None  None

In [5]:
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 150)

In [6]:
fights_data['R_SIG_STR_pct'] = fights_data['R_SIG_STR_pct'].str.strip('%').astype(float)
fights_data['B_SIG_STR_pct'] = fights_data['B_SIG_STR_pct'].str.strip('%').astype(float)
fights_data['R_TD_pct'] = fights_data['R_TD_pct'].str.strip('%').astype(float)
fights_data['B_TD_pct'] = fights_data['B_TD_pct'].str.strip('%').astype(float)

In [7]:
fights_data['R_SIG_STR_pct'] = fights_data['R_SIG_STR_pct']/100
fights_data['B_SIG_STR_pct'] = fights_data['B_SIG_STR_pct']/100
fights_data['R_TD_pct'] = fights_data['R_TD_pct']/100
fights_data['B_TD_pct'] = fights_data['B_TD_pct']/100


In [8]:
newfights_data = fights_data.drop(["R_TOTAL_STR.", "B_TOTAL_STR.", "R_TD", "B_TD"], axis=1)
newfights_data

R_fighter               B_fighter  R_KD  B_KD  R_SIG_STR.  B_SIG_STR.  R_SIG_STR_pct  B_SIG_STR_pct  R_TD_pct  B_TD_pct  \
0                  Henry Cejudo           Marlon Moraes   0.0   0.0   90 of 171   57 of 119           0.52           0.47      0.25      0.00   
1          Valentina Shevchenko             Jessica Eye   1.0   0.0     8 of 11     2 of 12           0.72           0.16      1.00      0.00   
2                 Tony Ferguson          Donald Cerrone   0.0   0.0  104 of 200   68 of 185           0.52           0.36      0.00      1.00   
3                 Jimmie Rivera                Petr Yan   0.0   2.0   73 of 192   56 of 189           0.38           0.29      0.00      0.33   
4                   Tai Tuivasa           Blagoy Ivanov   0.0   1.0   64 of 144   73 of 123           0.44           0.59      0.00      1.00   
5                Tatiana Suarez           Nina Ansaroff   0.0   0.0   75 of 142    48 of 99           0.52           0.48      0.30      0.00   
6             Aljamain Sterling            Pedro Munhoz   0.0   0.0  174 of 349  105 of 265           0.49           0.39      0.00      0.00   
7         Karolina Kowalkiewicz            Alexa Grasso   0.0   0.0   90 of 232  148 of 369           0.38           0.40      0.00      0.00   
8                 Ricardo Lamas           Calvin Kattar   0.0   1.0    12 of 29    22 of 41           0.41           0.53      0.00      0.00   
9                   Yan Xiaonan             Angela Hill   0.0   0.0   94 of 249   71 of 144           0.37           0.49      1.00      0.33   
10                  Bevon Lewis          Darren Stewart   0.0   0.0    31 of 84    30 of 73           0.36           0.41      0.00      0.00   
11               Eddie Wineland          Grigorii Popov   2.0   0.0   74 of 171   55 of 150           0.43           0.36      0.00      0.00   
12            Katlyn Chookagian       Joanne Calderwood   0.0   0.0   82 of 221  112 of 266           0.37           0.42      0.00      0.75   
13         Alexander Gustafsson           Anthony Smith   0.0   0.0   72 of 151   49 of 104           0.47           0.47      0.33      0.00   
14                  Jimi Manuwa        Aleksandar Rakic   0.0   1.0      2 of 3      2 of 7           0.66           0.28      0.00      0.00   
15             Makwan Amirkhani          Chris Fishgold   0.0   0.0     9 of 27    16 of 52           0.33           0.30      0.50      0.00   
16               Damir Hadzovic         Christos Giagos   0.0   0.0    24 of 61   47 of 113           0.39           0.41      1.00      0.46   
17                Daniel Teymur             Sung Bin Jo   0.0   0.0    40 of 83    21 of 63           0.48           0.33      0.16      0.33   
18                 Rostem Akman       Sergey Khandozhko   0.0   1.0   39 of 100   60 of 149           0.39           0.40      0.40      0.16   
19                Tonya Evinger           Lina Lansberg   0.0   0.0     6 of 11    50 of 68           0.54           0.73      0.25      0.50   
20                   Stevie Ray         Leonardo Santos   0.0   1.0     2 of 11    12 of 16           0.18           0.75      0.00      0.00   
21                    Nick Hein           Frank Camacho   0.0   0.0    37 of 79  100 of 201           0.46           0.49      0.33      0.00   
22                  Bea Malecki            Duda Santana   0.0   0.0    19 of 71   42 of 106           0.26           0.39      0.00      0.60   
23                 Darko Stosic             Devin Clark   0.0   0.0    26 of 55    40 of 95           0.47           0.42      0.33      0.18   
24                 Joel Alvarez        Danilo Belluardo   0.0   0.0    19 of 41    13 of 20           0.46           0.65      0.00      1.00   
25             Rafael Dos Anjos               Kevin Lee   0.0   0.0   60 of 111    35 of 97           0.54           0.36      0.57      0.37   
26        Antonio Carlos Junior            Ian Heinisch   0.0   0.0    15 of 33    39 of 67           0.45 

In [9]:
significant = newfights_data[['R_HEAD','B_HEAD','R_BODY','B_BODY','R_LEG','B_LEG','R_CLINCH','B_CLINCH','R_GROUND','B_GROUND']]
sig_col = significant.columns
sig_df = pd.DataFrame()

for col in sig_col:
    sig_series = significant[col].str.split(' of ', expand = True)
    sig_df[col] = sig_series[0].astype(float)/sig_series[1].astype(float)

sig_df = sig_df.fillna(0)
sig_df.head()

R_HEAD    B_HEAD    R_BODY    B_BODY     R_LEG     B_LEG  R_CLINCH  B_CLINCH  R_GROUND  B_GROUND
0  0.486667  0.393258  0.812500  0.875000  0.800000  0.681818  0.826087  1.000000  0.866667       1.0
1  0.800000  0.000000  0.666667  0.000000  0.000000  0.666667  1.000000  0.000000  1.000000       0.0
2  0.451389  0.282895  0.675676  0.652174  0.736842  1.000000  0.500000  0.000000  0.000000       0.0
3  0.289655  0.240964  0.625000  0.684211  0.695652  0.750000  0.600000  0.833333  1.000000       0.4
4  0.342105  0.570175  0.857143  0.875000  0.826087  1.000000  0.777778  0.833333  0.000000       1.0

In [10]:
temp_df1 = fights_data['R_TOTAL_STR.'].str.split(' of ', expand = True)
temp_df1['R_TOTAL_STR.'] = temp_df1[0].astype(float)/temp_df1[1].astype(float)

temp_df2 = fights_data['B_TOTAL_STR.'].str.split(' of ', expand = True)
temp_df2['B_TOTAL_STR.'] = temp_df2[0].astype(float)/temp_df2[1].astype(float)

temp_df3 = fights_data['R_TD'].str.split(' of ', expand = True)
temp_df3['R_TD'] = temp_df3[0].astype(float)/temp_df3[1].astype(float)

temp_df4 = fights_data['B_TD'].str.split(' of ', expand = True)
temp_df4['B_TD'] = temp_df3[0].astype(float)/temp_df3[1].astype(float)

In [11]:
newtemp_df1 = temp_df1.drop([0, 1], axis=1)
newtemp_df2 = temp_df2.drop([0, 1], axis=1)
newtemp_df3 = temp_df3.drop([0, 1], axis=1)
newtemp_df4 = temp_df4.drop([0, 1], axis=1)

In [12]:
df69 = newfights_data.join(newtemp_df1)
df70 = df69.join(newtemp_df2)
df71 = df70.join(newtemp_df3)
df72 = df71.join(newtemp_df4)
df72['new_column'] = np.where(df72['R_fighter'] == df72['Winner'], '0', '1')

In [13]:
df72 = df72.fillna(0).drop(['R_HEAD','B_HEAD','R_BODY','B_BODY','R_LEG','B_LEG','R_CLINCH','B_CLINCH','R_GROUND','B_GROUND'],axis=1)

In [14]:
df73 = df72.join(sig_df)
df73

R_fighter               B_fighter  R_KD  B_KD  R_SIG_STR.  B_SIG_STR.  R_SIG_STR_pct  B_SIG_STR_pct  R_TD_pct  B_TD_pct  \
0                  Henry Cejudo           Marlon Moraes   0.0   0.0   90 of 171   57 of 119           0.52           0.47      0.25      0.00   
1          Valentina Shevchenko             Jessica Eye   1.0   0.0     8 of 11     2 of 12           0.72           0.16      1.00      0.00   
2                 Tony Ferguson          Donald Cerrone   0.0   0.0  104 of 200   68 of 185           0.52           0.36      0.00      1.00   
3                 Jimmie Rivera                Petr Yan   0.0   2.0   73 of 192   56 of 189           0.38           0.29      0.00      0.33   
4                   Tai Tuivasa           Blagoy Ivanov   0.0   1.0   64 of 144   73 of 123           0.44           0.59      0.00      1.00   
5                Tatiana Suarez           Nina Ansaroff   0.0   0.0   75 of 142    48 of 99           0.52           0.48      0.30      0.00   
6             Aljamain Sterling            Pedro Munhoz   0.0   0.0  174 of 349  105 of 265           0.49           0.39      0.00      0.00   
7         Karolina Kowalkiewicz            Alexa Grasso   0.0   0.0   90 of 232  148 of 369           0.38           0.40      0.00      0.00   
8                 Ricardo Lamas           Calvin Kattar   0.0   1.0    12 of 29    22 of 41           0.41           0.53      0.00      0.00   
9                   Yan Xiaonan             Angela Hill   0.0   0.0   94 of 249   71 of 144           0.37           0.49      1.00      0.33   
10                  Bevon Lewis          Darren Stewart   0.0   0.0    31 of 84    30 of 73           0.36           0.41      0.00      0.00   
11               Eddie Wineland          Grigorii Popov   2.0   0.0   74 of 171   55 of 150           0.43           0.36      0.00      0.00   
12            Katlyn Chookagian       Joanne Calderwood   0.0   0.0   82 of 221  112 of 266           0.37           0.42      0.00      0.75   
13         Alexander Gustafsson           Anthony Smith   0.0   0.0   72 of 151   49 of 104           0.47           0.47      0.33      0.00   
14                  Jimi Manuwa        Aleksandar Rakic   0.0   1.0      2 of 3      2 of 7           0.66           0.28      0.00      0.00   
15             Makwan Amirkhani          Chris Fishgold   0.0   0.0     9 of 27    16 of 52           0.33           0.30      0.50      0.00   
16               Damir Hadzovic         Christos Giagos   0.0   0.0    24 of 61   47 of 113           0.39           0.41      1.00      0.46   
17                Daniel Teymur             Sung Bin Jo   0.0   0.0    40 of 83    21 of 63           0.48           0.33      0.16      0.33   
18                 Rostem Akman       Sergey Khandozhko   0.0   1.0   39 of 100   60 of 149           0.39           0.40      0.40      0.16   
19                Tonya Evinger           Lina Lansberg   0.0   0.0     6 of 11    50 of 68           0.54           0.73      0.25      0.50   
20                   Stevie Ray         Leonardo Santos   0.0   1.0     2 of 11    12 of 16           0.18           0.75      0.00      0.00   
21                    Nick Hein           Frank Camacho   0.0   0.0    37 of 79  100 of 201           0.46           0.49      0.33      0.00   
22                  Bea Malecki            Duda Santana   0.0   0.0    19 of 71   42 of 106           0.26           0.39      0.00      0.60   
23                 Darko Stosic             Devin Clark   0.0   0.0    26 of 55    40 of 95           0.47           0.42      0.33      0.18   
24                 Joel Alvarez        Danilo Belluardo   0.0   0.0    19 of 41    13 of 20           0.46           0.65      0.00      1.00   
25             Rafael Dos Anjos               Kevin Lee   0.0   0.0   60 of 111    35 of 97           0.54           0.36      0.57      0.37   
26        Antonio Carlos Junior            Ian Heinisch   0.0   0.0    15 of 33    39 of 67           0.45 

In [15]:
R_fighter_data = "UFC-DATA-DELETE-LATER/R_raw_fighter_details.csv"
R_fighter_df = pd.read_csv(R_fighter_data)
R_fighter_df_renamed = R_fighter_df.rename(columns={"fighter_name":"R_fighter", "Height":"R_Height", "Weight":"R_Weight", "Reach":"R_Reach", "Stance":"R_Stance", "DOB":"R_DOB"})
R_fighter_df_renamed.head()

R_fighter R_Height  R_Weight R_Reach R_Stance R_DOB
0   AJ Fonseca    5' 4"  145 lbs.     NaN      NaN   NaN
1  AJ Matthews   5' 11"  185 lbs.     NaN      NaN   NaN
2     AJ McKee   5' 10"  145 lbs.     NaN      NaN   NaN
3    AJ Siscoe    5' 7"  135 lbs.     NaN      NaN   NaN
4   Aalon Cruz    6' 0"  145 lbs.     NaN      NaN   NaN

In [16]:
B_fighter_data = "UFC-DATA-DELETE-LATER/B_raw_fighter_details.csv"
B_fighter_df = pd.read_csv(B_fighter_data)
B_fighter_df_renamed = B_fighter_df.rename(columns={"fighter_name":"B_fighter", "Height":"B_Height", "Weight":"B_Weight", "Reach":"B_Reach", "Stance":"B_Stance", "DOB":"B_DOB"})
B_fighter_df_renamed.head()

B_fighter B_Height  B_Weight B_Reach B_Stance B_DOB
0   AJ Fonseca    5' 4"  145 lbs.     NaN      NaN   NaN
1  AJ Matthews   5' 11"  185 lbs.     NaN      NaN   NaN
2     AJ McKee   5' 10"  145 lbs.     NaN      NaN   NaN
3    AJ Siscoe    5' 7"  135 lbs.     NaN      NaN   NaN
4   Aalon Cruz    6' 0"  145 lbs.     NaN      NaN   NaN

In [17]:
df73_B = pd.merge(df73, B_fighter_df_renamed, on="B_fighter")
df73_B

R_fighter              B_fighter  R_KD  B_KD  R_SIG_STR.  B_SIG_STR.  R_SIG_STR_pct  B_SIG_STR_pct  R_TD_pct  B_TD_pct  \
0                 Henry Cejudo          Marlon Moraes   0.0   0.0   90 of 171   57 of 119           0.52           0.47      0.25      0.00   
1             Raphael Assuncao          Marlon Moraes   0.0   1.0     2 of 12    10 of 23           0.16           0.43      0.00      0.00   
2                Jimmie Rivera          Marlon Moraes   0.0   1.0      0 of 3      7 of 9           0.00           0.77      0.00      0.00   
3                  John Dodson          Marlon Moraes   1.0   0.0   43 of 105   45 of 131           0.40           0.34      0.50      0.50   
4             Raphael Assuncao          Marlon Moraes   0.0   0.0   43 of 134   44 of 150           0.32           0.29      0.00      0.00   
5         Valentina Shevchenko            Jessica Eye   1.0   0.0     8 of 11     2 of 12           0.72           0.16      1.00      0.00   
6            Katlyn Chookagian            Jessica Eye   0.0   0.0   65 of 201   81 of 190           0.32           0.42      0.00      0.00   
7           Jessica-Rose Clark            Jessica Eye   0.0   0.0   51 of 139   67 of 225           0.36           0.29      0.00      0.50   
8               Kalindra Faria            Jessica Eye   0.0   0.0    38 of 70    25 of 49           0.54           0.51      0.50      0.75   
9                  Sara McMann            Jessica Eye   0.0   0.0    22 of 51    10 of 24           0.43           0.41      0.40      0.00   
10                 Miesha Tate            Jessica Eye   1.0   0.0   58 of 122   56 of 143           0.47           0.39      0.25      0.00   
11                Alexis Davis            Jessica Eye   0.0   0.0   53 of 113   47 of 111           0.46           0.42      0.66      0.00   
12               Sarah Kaufman            Jessica Eye   0.0   0.0   87 of 214   65 of 209           0.40           0.31      0.00      0.00   
13               Tony Ferguson         Donald Cerrone   0.0   0.0  104 of 200   68 of 185           0.52           0.36      0.00      1.00   
14                 Al Iaquinta         Donald Cerrone   0.0   2.0   90 of 223  138 of 361           0.40           0.38      0.00      0.00   
15         Alexander Hernandez         Donald Cerrone   0.0   1.0   49 of 105   80 of 162           0.46           0.49      0.00      1.00   
16               Robbie Lawler         Donald Cerrone   0.0   0.0   77 of 156   82 of 166           0.49           0.49      0.00      0.10   
17                  Rick Story         Donald Cerrone   0.0   1.0    17 of 51    45 of 73           0.33           0.61      0.20      1.00   
18            Rafael Dos Anjos         Donald Cerrone   0.0   0.0    26 of 44      4 of 7           0.59           0.57      0.00      0.00   
19              Anthony Pettis         Donald Cerrone   1.0   0.0    18 of 28     4 of 12           0.64           0.33      0.00      0.00   
20                   Nate Diaz         Donald Cerrone   0.0   0.0  238 of 362   96 of 182           0.65           0.52      0.00      0.00   
21                Dennis Siver         Donald Cerrone   0.0   2.0    12 of 21     9 of 23           0.57           0.39      0.00      0.00   
22                Vagner Rocha         Donald Cerrone   0.0   0.0   46 of 106   86 of 145           0.43           0.59      0.14      0.00   
23               Jimmie Rivera               Petr Yan   0.0   2.0   73 of 192   56 of 189           0.38           0.29      0.00      0.33   
24                 John Dodson               Petr Yan   1.0   0.0    30 of 81   80 of 155           0.37           0.51      0.25      0.40   
25    Douglas Silva de Andrade               Petr Yan   0.0   0.0    28 of 77   76 of 118           0.36           0.64      0.00      0.75   
26             Teruto Ishihara               Petr Yan   0.0   2.0    11 of 30    25 of 40           0.36           0.62      0.00      0.00   
27               

In [18]:
df73_B_R = pd.merge(df73_B, R_fighter_df_renamed, on="R_fighter")
df73_B_R_na = df73_B_R.dropna()

In [25]:
def parse_ht(ht):
    # format: 7' 0.0"
    ht_ = ht.split("' ")
    ft_ = float(ht_[0])
    in_ = float(ht_[1].replace("\"",""))
    return (12*ft_) + in_

inches_to_num = df73_B_R_na["R_Height"].apply(lambda x: parse_ht(x))


In [29]:
def parse_ht(ht):
    # format: 7' 0.0"
    ht_ = ht.split("' ")
    ft_ = float(ht_[0])
    in_ = float(ht_[1].replace("\"",""))
    return (12*ft_) + in_
inches_to_num_B = df73_B_R_na["B_Height"].apply(lambda x: parse_ht(x))
inches_to_num_B

0       66.0
1       66.0
2       66.0
3       64.0
4       66.0
5       67.0
6       66.0
7       66.0
8       66.0
9       67.0
10      66.0
11      67.0
12      68.0
13      68.0
14      67.0
15      66.0
16      66.0
17      65.0
18      66.0
19      67.0
20      67.0
21      63.0
22      67.0
23      66.0
24      67.0
25      66.0
26      65.0
27      66.0
28      67.0
29      67.0
30      65.0
31      64.0
32      66.0
33      66.0
34      67.0
35      66.0
37      66.0
38      66.0
39      66.0
40      69.0
41      66.0
43      66.0
44      68.0
45      66.0
46      67.0
47      66.0
48      68.0
49      66.0
50      65.0
51      66.0
52      68.0
53      67.0
54      66.0
55      61.0
56      66.0
57      66.0
58      66.0
59      64.0
60      69.0
61      66.0
62      67.0
63      65.0
64      63.0
65      66.0
66      65.0
67      69.0
68      73.0
69      69.0
70      70.0
71      70.0
72      69.0
73      70.0
74      68.0
75      69.0
76      68.0
77      70.0
78      69.0

In [191]:
# create date object using to_datetime() function
B_DOB_num = list(pd.to_datetime(df73_B_R_na["B_DOB"]))
R_DOB_num = list(pd.to_datetime(df73_B_R_na["R_DOB"]))
fight_date = list(pd.to_datetime(df73_B_R_na["date"]))


In [207]:
from datetime import timedelta, date

# Difference between two dates
# delta_B = (fight_date - B_DOB_num)
# delta_R = (fight_date - R_DOB_num)

from dateutil.relativedelta import relativedelta
#print(len(fight_date))
difference_in_years_B = [relativedelta(fight_date[i], B_DOB_num[i]).years for i in range(len(fight_date))]  
difference_in_years_R = [relativedelta(fight_date[i], R_DOB_num[i]).years for i in range(len(fight_date))]  

#difference_in_years = relativedelta(fight_date, B_DOB_num).years
#for fight_dates in fight_date

In [208]:
fight_date[36]

Timestamp('2018-12-08 00:00:00')

In [218]:
df73_B_R_na['R_Height'] = inches_to_num
df73_B_R_na['B_Height'] = inches_to_num_B
df73_B_R_na['date'] = fight_date
df73_B_R_na['age_at_fight_B'] = difference_in_years_B
df73_B_R_na['age_at_fight_R'] = difference_in_years_R

In [252]:
df73_B_R_na['B_Weight(lbs)'] = df73_B_R_na['B_Weight'].str.strip('lbs.')
df73_B_R_na['R_Weight(lbs)'] = df73_B_R_na['R_Weight'].str.strip('lbs.')
df73_B_R_na['R_Reach (inches)'] = df73_B_R_na['R_Reach'].str.strip('"')
df73_B_R_na['B_Reach (inches)'] = df73_B_R_na['B_Reach'].str.strip('"')
df73_B_R_na

R_fighter               B_fighter  R_KD  B_KD  R_SIG_STR.  B_SIG_STR.  R_SIG_STR_pct  B_SIG_STR_pct  R_TD_pct  B_TD_pct  \
0                 Henry Cejudo           Marlon Moraes   0.0   0.0   90 of 171   57 of 119           0.52           0.47      0.25      0.00   
1                 Henry Cejudo            TJ Dillashaw   1.0   0.0    18 of 23      1 of 3           0.78           0.33      0.00      0.00   
2                 Henry Cejudo           Sergio Pettis   0.0   0.0    36 of 83    25 of 98           0.43           0.25      0.60      0.00   
3                 Henry Cejudo             Wilson Reis   1.0   0.0    34 of 58     5 of 25           0.58           0.20      1.00      0.00   
4                 Henry Cejudo             Chico Camus   0.0   0.0   62 of 143   48 of 144           0.43           0.33      0.06      0.00   
5                 Henry Cejudo           Dustin Kimura   1.0   0.0   72 of 145   25 of 161           0.49           0.15      0.00      0.00   
6             Raphael Assuncao           Marlon Moraes   0.0   1.0     2 of 12    10 of 23           0.16           0.43      0.00      0.00   
7             Raphael Assuncao           Marlon Moraes   0.0   0.0   43 of 134   44 of 150           0.32           0.29      0.00      0.00   
8             Raphael Assuncao            Pedro Munhoz   0.0   0.0  100 of 206   33 of 100           0.48           0.33      1.00      0.00   
9             Raphael Assuncao       Aljamain Sterling   0.0   0.0   39 of 101   52 of 172           0.38           0.30      0.00      0.00   
10            Raphael Assuncao            TJ Dillashaw   0.0   0.0   32 of 101   29 of 101           0.31           0.28      0.00      0.50   
11            Raphael Assuncao           Matthew Lopez   1.0   0.0   46 of 154    34 of 93           0.29           0.36      0.00      0.25   
12            Raphael Assuncao           Bryan Caraway   0.0   0.0   75 of 133   39 of 128           0.56           0.30      0.33      0.25   
13            Raphael Assuncao                Rob Font   0.0   0.0   54 of 120   20 of 122           0.45           0.16      1.00      0.00   
14            Raphael Assuncao          Johnny Eduardo   0.0   0.0   53 of 101    28 of 85           0.52           0.32      0.37      0.00   
15            Raphael Assuncao             Vaughan Lee   0.0   0.0    17 of 54    14 of 27           0.31           0.51      0.60      0.00   
16            Raphael Assuncao             Mike Easton   0.0   0.0   57 of 156   30 of 155           0.36           0.19      0.00      0.00   
17            Raphael Assuncao            Issei Tamura   1.0   0.0    39 of 60     5 of 14           0.65           0.35      0.00      0.00   
18               Jimmie Rivera           Marlon Moraes   0.0   1.0      0 of 3      7 of 9           0.00           0.77      0.00      0.00   
19               Jimmie Rivera                Petr Yan   0.0   2.0   73 of 192   56 of 189           0.38           0.29      0.00      0.33   
20               Jimmie Rivera       Aljamain Sterling   0.0   0.0    24 of 84  101 of 176           0.28           0.57      0.00      0.00   
21               Jimmie Rivera             John Dodson   0.0   0.0   62 of 125   41 of 117           0.49           0.35      0.00      0.00   
22               Jimmie Rivera          Thomas Almeida   2.0   0.0   70 of 160   72 of 167           0.43           0.43      0.33      0.00   
23                 John Dodson           Marlon Moraes   1.0   0.0   43 of 105   45 of 131           0.40           0.34      0.50      0.50   
24                 John Dodson                Petr Yan   1.0   0.0    30 of 81   80 of 155           0.37           0.51      0.25      0.40   
25                 John Dodson            Pedro Munhoz   0.0   0.0   76 of 184   69 of 172           0.41           0.40      0.00      1.00   
26                 John Dodson         Jussier Formiga   2.0   0.0   33 of 112     9 of 37           0.29           0.24      0.00   

In [265]:
# Creating input feature
X = df72[['R_KD','B_KD','R_SIG_STR_pct', 'B_SIG_STR_pct', 'R_TOTAL_STR.', 'B_TOTAL_STR.',
                 'R_TD','B_TD','R_TD_pct','B_TD_pct','R_SUB_ATT','B_SUB_ATT','R_PASS','B_PASS','R_REV','B_REV']]

X2 = df73[['R_KD','B_KD','R_HEAD','R_TD','B_TD',
           'B_HEAD','R_BODY','B_BODY','R_LEG','B_LEG','R_CLINCH',
           'B_CLINCH','R_GROUND','B_GROUND','R_SUB_ATT','B_SUB_ATT']]

X3 = df73_B_R_na[['R_KD','B_KD','R_HEAD','R_TD','B_TD',
           'B_HEAD','R_BODY','B_BODY','R_LEG','B_LEG','R_CLINCH',
           'B_CLINCH','R_GROUND','B_GROUND','R_SUB_ATT','B_SUB_ATT','R_Height','B_Height',
           'age_at_fight_B','age_at_fight_R','R_Reach (inches)','B_Reach (inches)' ]]

# Creating target variable
y = df72[['new_column']]
y2 = df73_B_R_na[['new_column']]

#Creating Train and Test dataset
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X3, y2, test_size=0.3)

# #Normalizing the input features
# from sklearn.preprocessing import StandardScaler
# sc_x = StandardScaler()
# X_train = sc_x.fit_transform(X_train)
# X_test = sc_x.transform(X_test)

# #Normalizing the target variable
# sc_y = StandardScaler()
# y_train = sc_y.fit_transform(y_train)
# y_test = sc_y.transform(y_test)

# Creating the Logistic regressor
classifier = LogisticRegression()

# fitting the training data to the Logistic Regressor
classifier.fit(X_train,y_train)

# Checking the model coefficients
classifier.coef_

C:\Users\acer\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\acer\Anaconda3\lib\site-packages\sklearn\utils\validation.py:724: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


array([[-1.26948037,  1.04400134, -3.47217475, -0.59369399, -0.59369399,
         3.85174483, -0.18260989,  0.30217864, -0.43217971,  0.33621639,
         0.21278379, -0.02196881, -0.5626622 ,  0.98176184, -0.50582686,
         0.28090784, -0.04441864,  0.01094798, -0.01918069,  0.06842269,
        -0.02851627,  0.03165624]])

In [266]:
LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='ovr', n_jobs=1,
          penalty='l2', random_state=None, solver='liblinear', tol=0.0001,
          verbose=0, warm_start=False)

LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
                   intercept_scaling=1, l1_ratio=None, max_iter=100,
                   multi_class='ovr', n_jobs=1, penalty='l2', random_state=None,
                   solver='liblinear', tol=0.0001, verbose=0, warm_start=False)

In [267]:
classifier.fit(X_train, y_train)
test_results = classifier.predict(X_test)
print(f"Training Data Score: {classifier.score(X_train, y_train)}")
print(f"Testing Data Score: {classifier.score(X_test, y_test)}")

Training Data Score: 0.8006155950752394
Testing Data Score: 0.8046251993620415


C:\Users\acer\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)
C:\Users\acer\Anaconda3\lib\site-packages\sklearn\utils\validation.py:724: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


In [268]:
predictions = classifier.predict(X_test)
print(f"First 10 Predictions:   {predictions[:10]}")
print(f"First 10 Actual labels: {y_test[:10].values.tolist()}")

First 10 Predictions:   ['0' '0' '1' '0' '0' '0' '1' '0' '0' '0']
First 10 Actual labels: [['0'], ['1'], ['0'], ['0'], ['0'], ['0'], ['1'], ['1'], ['1'], ['1']]


In [269]:
accuracy = classifier.score(X_test, y_test)
print('The accuracy is: ' + str(accuracy *100) + '%')

The accuracy is: 80.46251993620415%


In [272]:
pd.DataFrame({"Prediction": predictions, "Actual": y_test['new_column']}).reset_index(drop=True)
# function for predictions

def predict(model, R_figher, B_figher):
    data1 = fighers_clean.loc[figher1, statistics]
    data2 = fighers_clean.loc[figher2, statistics]
    data_diff = (data1 - data2).values.reshape(1, -1)
    data_diff_scaled = scaler.transform(data_diff)
    return model.predict(data_diff_scaled)

print(predict(model, "Cub Swanson", "Brian Ortega"))

NameError: name 'model' is not defined

In [271]:
from sklearn.metrics import confusion_matrix
confusion_matrix = confusion_matrix(predictions, y_test)
print(confusion_matrix)

[[709 152]
 [ 93 300]]
